In [1]:
import numpy as np
import os 
import pandas as pd
import cv2
import torch
import matplotlib.pyplot as plt
from ipywidgets import interact
import albumentations as A
from albumentations.pytorch import ToTensorV2
import torchvision
from torch import nn
import torchsummary
from torch.utils.data import DataLoader
from collections import defaultdict
from torchvision.utils import make_grid

In [2]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
device

device(type='cuda', index=0)

## Utils

In [3]:
CLASS_NAME_TO_ID = {'Unformed': 0, 'Burr': 1}
CLASS_ID_TO_NAME = {0: 'Unformed', 1: 'Burr'}
BOX_COLOR = {'Unformed':(200, 0, 0), 'Burr':(0, 0, 200)}
TEXT_COLOR = (255, 255, 255)

def save_model(model_state, model_name, save_dir="./trained_model"):
    os.makedirs(save_dir, exist_ok=True)
    torch.save(model_state, os.path.join(save_dir, model_name))


def visualize_bbox(image, bbox, class_name, color=BOX_COLOR, thickness=2):
    x_center, y_center, w, h = bbox
    x_min = int(x_center - w/2)
    y_min = int(y_center - h/2)
    x_max = int(x_center + w/2)
    y_max = int(y_center + h/2)
    
    cv2.rectangle(image, (x_min, y_min), (x_max, y_max), color=color[class_name], thickness=thickness)
    
    ((text_width, text_height), _) = cv2.getTextSize(class_name, cv2.FONT_HERSHEY_SIMPLEX, 0.35, 1)    
    cv2.rectangle(image, (x_min, y_min - int(1.3 * text_height)), (x_min + text_width, y_min), color[class_name], -1)
    cv2.putText(
        image,
        text=class_name,
        org=(x_min, y_min - int(0.3 * text_height)),
        fontFace=cv2.FONT_HERSHEY_SIMPLEX,
        fontScale=0.35, 
        color=TEXT_COLOR, 
        lineType=cv2.LINE_AA,
    )
    return image


def visualize(image, bboxes, category_ids):
    img = image.copy()
    for bbox, category_id in zip(bboxes, category_ids):
#         print('category_id: ',category_id)
        class_name = CLASS_ID_TO_NAME[category_id.item()]
        img = visualize_bbox(img, bbox, class_name)
    return img

## Datasets

In [4]:
class PET_dataset():
    def __init__(self,part,neck_dir,body_dir,phase, transformer=None, aug=None, aug_factor=0):
        self.neck_dir=neck_dir
        self.body_dir=body_dir
        self.part=part
        self.phase=phase
        self.transformer=transformer
        self.aug=aug
        self.aug_factor=aug_factor
        if(self.part=="body"):
            self.image_files = sorted([fn for fn in os.listdir(self.body_dir+"/"+self.phase+"/image") if fn.endswith("jpg")])
            self.label_files= sorted([lab for lab in os.listdir(self.body_dir+"/"+self.phase+"/label") if lab.endswith("txt")])
        elif(self.part=="neck"):
            self.image_files = sorted([fn for fn in os.listdir(self.neck_dir+"/"+self.phase+"/image") if fn.endswith("jpg")])
            self.label_files= sorted([lab for lab in os.listdir(self.neck_dir+"/"+self.phase+"/label") if lab.endswith("txt")])
        
        self.auged_img_list, self.auged_label_list=self.make_aug_list(self.image_files, self.label_files)
        
    def __getitem__(self,index):
        if(self.aug==None):
            filename, image = self.get_image(self.part, index)
            bboxes, class_ids = self.get_label(self.part, index)

            if(self.transformer):
                transformed_data=self.transformer(image=image, bboxes=bboxes, class_ids=class_ids)
                image = transformed_data['image']
                bboxes = np.array(transformed_data['bboxes'])
                class_ids = np.array(transformed_data['class_ids'])


            target = {}
    #         print(f'bboxes:{bboxes}\nclass_ids:{class_ids}\nlen_bboxes:{len(bboxes)}\nlen_class_ids:{len(class_ids)}')
    #         print(f'filename: {filename}')
            target["boxes"] = torch.Tensor(bboxes).float()
            target["labels"] = torch.Tensor(class_ids).long()

            ###
            bboxes=torch.Tensor(bboxes).float()
            class_ids=torch.Tensor(class_ids).long()
            target = np.concatenate((bboxes, class_ids[:, np.newaxis]), axis=1)
            ###
        else:
            image=self.auged_img_list[index][1]
            target=self.auged_label_list[index]
            filename=self.auged_img_list[index][0]
        return image, target, filename
    
    def __len__(self, ):
        length=0
        if(self.aug==None):
            length=len(self.image_files)
        else:
            length=len(self.auged_img_list)
        return length
    
    def make_aug_list(self,ori_image_list,ori_label_files):
        aug_image_list=[]
        aug_label_list=[]
        
        print(f"start making augmented images-- augmented factor:{self.aug_factor}")
        for i in range(len(ori_image_list)):
            filename, ori_image = self.get_image(self.part, i)
            ori_bboxes, ori_class_ids = self.get_label(self.part, i)
#             print(f"{filename}--------------\n{ori_bboxes}")
            for j in range(self.aug_factor):
                auged_data=self.aug(image=ori_image, bboxes=ori_bboxes, class_ids=ori_class_ids)
                image = auged_data['image']
                bboxes = np.array(auged_data['bboxes'])
                class_ids = np.array(auged_data['class_ids'])
                
                bboxes=torch.Tensor(bboxes).float()
                class_ids=torch.Tensor(class_ids).long()
                
                aug_image_list.append((filename, image))
                aug_label_list.append(np.concatenate((bboxes, class_ids[:, np.newaxis]), axis=1))
        
        print(f"total length of augmented images: {len(aug_image_list)}")
        
        return aug_image_list, aug_label_list
        
    
    def get_image(self, part, index): # 이미지 불러오는 함수
        filename = self.image_files[index]
        if(part=="body"):
#             print(f"body called!-> {self.part}")
            image_path = self.body_dir+"/"+self.phase+"/image/"+filename
        elif(part=="neck"):
#             print(f"neck called!-> {self.part}")
            image_path = self.neck_dir+"/"+self.phase+"/image/"+filename
        image = cv2.imread(image_path)
        image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
        return filename, image
    
    def get_label(self, part, index): # label (box좌표, class_id) 불러오는 함수
        label_filename=self.label_files[index]
        if(part=="body"):
#             print(f"body label called!-> {self.part}")
            label_path = self.body_dir+"/"+self.phase+"/label/"+label_filename
        elif(part=="neck"):
#             print(f"neck label called!-> {self.part}")
            label_path = self.neck_dir+"/"+self.phase+"/label/"+label_filename
        with open(label_path, 'r') as file:
            labels = file.readlines()
        
        class_ids=[]
        bboxes=[]
        for label in labels:
            label=label.replace("\n", "")
            obj=label.split(' ')[0]
            coor=label.split(' ')[1:]
            obj=int(obj)
            coor=list(map(float, coor))
            class_ids.append(obj)
            bboxes.append(coor)
            
        return bboxes, class_ids
    

In [5]:
IMAGE_SIZE = 448

transformer = A.Compose([ 
        # bounding box의 변환, augmentation에서 albumentations는 Detection 학습을 할 때 굉장히 유용하다. 
        A.Resize(height=IMAGE_SIZE, width=IMAGE_SIZE),
        A.Normalize(mean=(0.485, 0.456, 0.406),std=(0.229, 0.224, 0.225)),
        ToTensorV2(),
        # albumentations 라이브러리에서는 Normalization을 먼저 진행해 주고 tensor화를 진행해 주어야한다.
    ],
    # box 위치에 대한 transformation도 함께 진행된다. 
    bbox_params=A.BboxParams(format='yolo', label_fields=['class_ids']),
)

augmentator=A.Compose([
#     A.Resize(height=IMAGE_SIZE, width=IMAGE_SIZE),
    A.HorizontalFlip(p=0.7),
    A.Sharpen(p=0.7),
#     A.RandomSizedBBoxSafeCrop(height=IMAGE_SIZE, width=IMAGE_SIZE, p=1),
    A.VerticalFlip (p=0.5),
#     A.HueSaturationValue(p=0.5),
#     A.Resize(height=IMAGE_SIZE, width=IMAGE_SIZE),
#     A.Normalize(mean=(0.485, 0.456, 0.406),std=(0.229, 0.224, 0.225)),
#     ToTensorV2(),
    ],
    bbox_params=A.BboxParams(format='yolo', label_fields=['class_ids']),
)

def collate_fn(batch):
    image_list = []
    target_list = []
    filename_list = []
    
    for a,b,c in batch:
        image_list.append(a)
        target_list.append(b)
        filename_list.append(c)

    return torch.stack(image_list, dim=0), target_list, filename_list


In [6]:
NECK_PATH = '/home/host_data/PET_data_image_patching/patched_Neck/'
BODY_PATH = '/home/host_data/PET_data/Body'

trainset_IP_AUG=PET_dataset(part='neck',neck_dir=NECK_PATH,body_dir=BODY_PATH,phase='valid', transformer=transformer, aug=augmentator, aug_factor=2)



start making augmented images-- augmented factor:2
total length of augmented images: 3600


In [7]:
PHASE='train'

_, _, temp_filename=trainset_IP_AUG[0]
file_num=2
for i in range(len(trainset_IP_AUG)):
    image, target, filename = trainset_IP_AUG[i]
    if(temp_filename==filename):
        file_num=file_num+1
    else:
        file_num=3
    temp_filename=filename
    file_title=filename.split(".")[0]
    save_title=f"{file_title}_aug{file_num}"
    
    #이미지 저장
    cv2.imwrite(f"/home/host_data/PET_data_IP_AUG/aug_patched_Neck/{PHASE}/image/"+save_title+".jpg", image)
        
    #라벨파일 저장
    f = open(f"/home/host_data/PET_data_IP_AUG/aug_patched_Neck/{PHASE}/label/"+save_title+".txt", 'w')
    print(f"ori-tar:{target}")
    for j in range(len(target)):
        write_str=f"{int(target[j][4])} {target[j][0]} {target[j][1]} {target[j][2]} {target[j][3]}\n"
        print(write_str)
        f.write(write_str)

    print(save_title)
#     print(str(target).replace("[", " ").replace("]", " "))
    print(target)

ori-tar:[[0.17665756 0.30400056 0.06505054 0.15200026 0.        ]
 [0.17602062 0.54400021 0.05612246 0.14399956 0.        ]]
0 0.1766575574874878 0.3040005564689636 0.06505054235458374 0.15200026333332062

0 0.17602062225341797 0.5440002083778381 0.05612246319651604 0.14399956166744232

shape1_102_aug1_aug3
[[0.17665756 0.30400056 0.06505054 0.15200026 0.        ]
 [0.17602062 0.54400021 0.05612246 0.14399956 0.        ]]
ori-tar:[[0.17665756 0.30400056 0.06505054 0.15200026 0.        ]
 [0.17602062 0.54400021 0.05612246 0.14399956 0.        ]]
0 0.1766575574874878 0.3040005564689636 0.06505054235458374 0.15200026333332062

0 0.17602062225341797 0.5440002083778381 0.05612246319651604 0.14399956166744232

shape1_102_aug1_aug4
[[0.17665756 0.30400056 0.06505054 0.15200026 0.        ]
 [0.17602062 0.54400021 0.05612246 0.14399956 0.        ]]
ori-tar:[[0.11469293 0.77941108 0.05391081 0.18627483 0.        ]
 [0.11416507 0.48529387 0.04651164 0.17647006 0.        ]]
0 0.11469292640686035 0

ori-tar:[[0.24067533 0.48919672 0.05646885 0.18326066 0.        ]]
0 0.24067533016204834 0.4891967177391052 0.05646884813904762 0.18326066434383392

shape1_104_aug7_aug3
[[0.24067533 0.48919672 0.05646885 0.18326066 0.        ]]
ori-tar:[[0.75932467 0.51080328 0.05646885 0.18326066 0.        ]]
0 0.7593246698379517 0.5108032822608948 0.05646884813904762 0.18326066434383392

shape1_104_aug7_aug4
[[0.75932467 0.51080328 0.05646885 0.18326066 0.        ]]
ori-tar:[[0.90986675 0.45924479 0.1393173  0.18738815 0.        ]]
0 0.9098667502403259 0.4592447876930237 0.13931730389595032 0.18738815188407898

shape1_104_aug8_aug3
[[0.90986675 0.45924479 0.1393173  0.18738815 0.        ]]
ori-tar:[[0.90986675 0.54075521 0.1393173  0.18738815 0.        ]]
0 0.9098667502403259 0.5407552123069763 0.13931730389595032 0.18738815188407898

shape1_104_aug8_aug4
[[0.90986675 0.54075521 0.1393173  0.18738815 0.        ]]
ori-tar:[[0.23065513 0.60815459 0.20304756 0.27189654 0.        ]]
0 0.2306551337242126

ori-tar:[[0.61862481 0.40217417 0.05321472 0.14492778 0.        ]
 [0.61751711 0.6557976  0.04656288 0.12318806 0.        ]]
0 0.6186248064041138 0.402174174785614 0.053214721381664276 0.14492778480052948

0 0.6175171136856079 0.6557976007461548 0.046562884002923965 0.12318805605173111

shape1_108_aug7_aug4
[[0.61862481 0.40217417 0.05321472 0.14492778 0.        ]
 [0.61751711 0.6557976  0.04656288 0.12318806 0.        ]]
ori-tar:[[0.63876593 0.18556744 0.07048411 0.20618592 0.        ]
 [0.6372987  0.54639244 0.0616736  0.17525724 0.        ]]
0 0.6387659311294556 0.1855674386024475 0.07048410922288895 0.20618592202663422

0 0.6372987031936646 0.5463924407958984 0.0616735965013504 0.17525723576545715

shape1_108_aug8_aug3
[[0.63876593 0.18556744 0.07048411 0.20618592 0.        ]
 [0.6372987  0.54639244 0.0616736  0.17525724 0.        ]]
ori-tar:[[0.63876593 0.18556744 0.07048411 0.20618592 0.        ]
 [0.6372987  0.54639244 0.0616736  0.17525724 0.        ]]
0 0.6387659311294556 0.18

ori-tar:[[0.33703113 0.56159449 0.27184382 0.4420287  0.        ]]
0 0.33703112602233887 0.5615944862365723 0.271843820810318 0.4420287013053894

shape1_112_aug10_aug4
[[0.33703113 0.56159449 0.27184382 0.4420287  0.        ]]
ori-tar:[[0.44954008 0.53525662 0.4495399  0.39102539 0.        ]]
0 0.44954007863998413 0.5352566242218018 0.4495398998260498 0.3910253942012787

shape1_112_aug11_aug3
[[0.44954008 0.53525662 0.4495399  0.39102539 0.        ]]
ori-tar:[[0.44954008 0.46474338 0.4495399  0.39102539 0.        ]]
0 0.44954007863998413 0.46474337577819824 0.4495398998260498 0.3910253942012787

shape1_112_aug11_aug4
[[0.44954008 0.46474338 0.4495399  0.39102539 0.        ]]
ori-tar:[[0.19481808 0.79145712 0.20310818 0.30653247 0.        ]]
0 0.19481807947158813 0.7914571166038513 0.20310817658901215 0.30653247237205505

shape1_112_aug12_aug3
[[0.19481808 0.79145712 0.20310818 0.30653247 0.        ]]
ori-tar:[[0.19481808 0.79145712 0.20310818 0.30653247 0.        ]]
0 0.194818079471588

ori-tar:[[0.43537796 0.5156244  0.31462124 0.74999893 0.        ]]
0 0.43537795543670654 0.5156244039535522 0.314621239900589 0.749998927116394

shape1_117_aug14_aug3
[[0.43537796 0.5156244  0.31462124 0.74999893 0.        ]]
ori-tar:[[0.43537796 0.4843756  0.31462124 0.74999893 0.        ]]
0 0.43537795543670654 0.48437559604644775 0.314621239900589 0.749998927116394

shape1_117_aug14_aug4
[[0.43537796 0.4843756  0.31462124 0.74999893 0.        ]]
ori-tar:[[0.61531097 0.63636398 0.46705401 0.36363584 0.        ]]
0 0.6153109669685364 0.6363639831542969 0.46705400943756104 0.3636358380317688

shape1_117_aug15_aug3
[[0.61531097 0.63636398 0.46705401 0.36363584 0.        ]]
ori-tar:[[0.38468903 0.63636398 0.46705401 0.36363584 0.        ]]
0 0.3846890330314636 0.6363639831542969 0.46705400943756104 0.3636358380317688

shape1_117_aug15_aug4
[[0.38468903 0.63636398 0.46705401 0.36363584 0.        ]]
ori-tar:[[0.62334359 0.74193573 0.3990064  0.25806415 0.        ]]
0 0.6233435869216919 0.7

...

ori-tar:[[0.16747589 0.41758263 0.10517833 0.24175863 0.        ]]
0 0.1674758940935135 0.417582631111145 0.1051783338189125 0.24175862967967987

shape6_20_aug10_aug3
[[0.16747589 0.41758263 0.10517833 0.24175863 0.        ]]
ori-tar:[[0.83252412 0.41758263 0.10517833 0.24175863 0.        ]]
0 0.8325241208076477 0.417582631111145 0.1051783338189125 0.24175862967967987

shape6_20_aug10_aug4
[[0.83252412 0.41758263 0.10517833 0.24175863 0.        ]]
ori-tar:[[0.94075292 0.80666691 0.07198251 0.2933338  0.        ]]
0 0.9407529234886169 0.806666910648346 0.07198251038789749 0.2933337986469269

shape6_20_aug11_aug3
[[0.94075292 0.80666691 0.07198251 0.2933338  0.        ]]
ori-tar:[[0.05924707 0.80666691 0.07198251 0.2933338  0.        ]]
0 0.05924706906080246 0.806666910648346 0.07198251038789749 0.2933337986469269

shape6_20_aug11_aug4
[[0.05924707 0.80666691 0.07198251 0.2933338  0.        ]]
ori-tar:[[0.9585833  0.49407101 0.07803147 0.17391331 0.        ]]
0 0.9585832953453064 0.49407

ori-tar:[[0.03163081 0.15983552 0.03649666 0.28688607 0.        ]]
0 0.03163081407546997 0.15983551740646362 0.036496661603450775 0.286886066198349

shape6_22_aug16_aug3
[[0.03163081 0.15983552 0.03649666 0.28688607 0.        ]]
ori-tar:[[0.03163081 0.84016448 0.03649666 0.28688607 0.        ]]
0 0.03163081407546997 0.8401644825935364 0.036496661603450775 0.286886066198349

shape6_22_aug16_aug4
[[0.03163081 0.84016448 0.03649666 0.28688607 0.        ]]
ori-tar:[[0.97432846 0.26923066 0.03500613 0.53846133 0.        ]]
0 0.9743284583091736 0.2692306637763977 0.03500613197684288 0.5384613275527954

shape6_22_aug17_aug3
[[0.97432846 0.26923066 0.03500613 0.53846133 0.        ]]
ori-tar:[[0.02567154 0.26923066 0.03500613 0.53846133 0.        ]]
0 0.025671541690826416 0.2692306637763977 0.03500613197684288 0.5384613275527954

shape6_22_aug17_aug4
[[0.02567154 0.26923066 0.03500613 0.53846133 0.        ]]
ori-tar:[[0.03108311 0.23764282 0.03215462 0.13308023 0.        ]]
0 0.0310831069946289

ori-tar:[[0.31415963 0.4928053  0.10619508 0.11510795 0.        ]]
0 0.314159631729126 0.4928053021430969 0.10619507730007172 0.1151079460978508

shape6_36_aug22_aug3
[[0.31415963 0.4928053  0.10619508 0.11510795 0.        ]]
ori-tar:[[0.31415963 0.5071947  0.10619508 0.11510795 0.        ]]
0 0.314159631729126 0.5071946978569031 0.10619507730007172 0.1151079460978508

shape6_36_aug22_aug4
[[0.31415963 0.5071947  0.10619508 0.11510795 0.        ]]
ori-tar:[[0.39238673 0.40167415 0.07027844 0.13389124 0.        ]]
0 0.3923867344856262 0.40167415142059326 0.07027844339609146 0.1338912397623062

shape6_36_aug23_aug3
[[0.39238673 0.40167415 0.07027844 0.13389124 0.        ]]
ori-tar:[[0.39238673 0.59832585 0.07027844 0.13389124 0.        ]]
0 0.3923867344856262 0.5983258485794067 0.07027844339609146 0.1338912397623062

shape6_36_aug23_aug4
[[0.39238673 0.59832585 0.07027844 0.13389124 0.        ]]
ori-tar:[[0.35890788 0.5644604  0.06241896 0.11149829 0.        ]]
0 0.35890787839889526 0.56

ori-tar:[[0.38049459 0.61940211 0.19505341 0.58209038 0.        ]]
0 0.3804945945739746 0.6194021105766296 0.19505341351032257 0.5820903778076172

shape6_4_aug28_aug3
[[0.38049459 0.61940211 0.19505341 0.58209038 0.        ]]
ori-tar:[[0.61950541 0.38059789 0.19505341 0.58209038 0.        ]]
0 0.6195054054260254 0.38059788942337036 0.19505341351032257 0.5820903778076172

shape6_4_aug28_aug4
[[0.61950541 0.38059789 0.19505341 0.58209038 0.        ]]
ori-tar:[[0.56376803 0.20937462 0.2057955  0.24375035 0.        ]]
0 0.5637680292129517 0.20937462151050568 0.2057954967021942 0.24375034868717194

shape6_4_aug29_aug3
[[0.56376803 0.20937462 0.2057955  0.24375035 0.        ]]
ori-tar:[[0.43623197 0.20937462 0.2057955  0.24375035 0.        ]]
0 0.43623197078704834 0.20937462151050568 0.2057954967021942 0.24375034868717194

shape6_4_aug29_aug4
[[0.43623197 0.20937462 0.2057955  0.24375035 0.        ]]
ori-tar:[[0.20631421 0.2819764  0.10425763 0.22674452 0.        ]]
0 0.20631420612335205 0.2

ori-tar:[[0.36786908 0.76153827 0.20720716 0.19999991 0.        ]]
0 0.3678690791130066 0.7615382671356201 0.20720715820789337 0.19999991357326508

shape6_7_aug33_aug4
[[0.36786908 0.76153827 0.20720716 0.19999991 0.        ]]
ori-tar:[[0.46224064 0.22115362 0.17968746 0.2499999  0.        ]]
0 0.46224063634872437 0.2211536169052124 0.17968745529651642 0.24999989569187164

shape6_7_aug34_aug3
[[0.46224064 0.22115362 0.17968746 0.2499999  0.        ]]
ori-tar:[[0.53775936 0.77884638 0.17968746 0.2499999  0.        ]]
0 0.5377593636512756 0.7788463830947876 0.17968745529651642 0.24999989569187164

shape6_7_aug34_aug4
[[0.53775936 0.77884638 0.17968746 0.2499999  0.        ]]
ori-tar:[[0.67458761 0.41216168 0.14256194 0.52702677 0.        ]]
0 0.674587607383728 0.4121616780757904 0.14256194233894348 0.5270267724990845

shape6_7_aug35_aug3
[[0.67458761 0.41216168 0.14256194 0.52702677 0.        ]]
ori-tar:[[0.67458761 0.58783829 0.14256194 0.52702677 0.        ]]
0 0.674587607383728 0.5878

In [7]:
PHASE='valid'

_, _, temp_filename=trainset_IP_AUG[0]
file_num=2
for i in range(len(trainset_IP_AUG)):
    image, target, filename = trainset_IP_AUG[i]
    if(temp_filename==filename):
        file_num=file_num+1
    else:
        file_num=3
    temp_filename=filename
    file_title=filename.split(".")[0]
    save_title=f"{file_title}_aug{file_num}"
    
    #이미지 저장
    cv2.imwrite(f"/home/host_data/PET_data_IP_AUG/aug_patched_Neck/{PHASE}/image/"+save_title+".jpg", image)
        
    #라벨파일 저장
    f = open(f"/home/host_data/PET_data_IP_AUG/aug_patched_Neck/{PHASE}/label/"+save_title+".txt", 'w')
    print(f"ori-tar:{target}")
    for j in range(len(target)):
        write_str=f"{int(target[j][4])} {target[j][0]} {target[j][1]} {target[j][2]} {target[j][3]}\n"
        print(write_str)
        f.write(write_str)

    print(save_title)
#     print(str(target).replace("[", " ").replace("]", " "))
    print(target)

ori-tar:[[0.54485112 0.33800048 0.14617775 0.12399958 0.        ]
 [0.54651153 0.58800042 0.14285703 0.14400026 0.        ]]
0 0.5448511242866516 0.33800047636032104 0.1461777538061142 0.12399958074092865

0 0.5465115308761597 0.5880004167556763 0.14285703003406525 0.14400026202201843

shape1_101_aug1_aug3
[[0.54485112 0.33800048 0.14617775 0.12399958 0.        ]
 [0.54651153 0.58800042 0.14285703 0.14400026 0.        ]]
ori-tar:[[0.54485112 0.66199952 0.14617775 0.12399958 0.        ]
 [0.54651153 0.41199958 0.14285703 0.14400026 0.        ]]
0 0.5448511242866516 0.661999523639679 0.1461777538061142 0.12399958074092865

0 0.5465115308761597 0.41199958324432373 0.14285703003406525 0.14400026202201843

shape1_101_aug1_aug4
[[0.54485112 0.66199952 0.14617775 0.12399958 0.        ]
 [0.54651153 0.41199958 0.14285703 0.14400026 0.        ]]
ori-tar:[[0.88141835 0.27871662 0.05378912 0.10472938 0.        ]
 [0.88202929 0.48986524 0.05256719 0.12162184 0.        ]]
0 0.8814183473587036 0.278

ori-tar:[[0.06428619 0.59929061 0.04285699 0.24822687 0.        ]]
0 0.06428618729114532 0.5992906093597412 0.042856987565755844 0.24822686612606049

shape1_103_aug9_aug3
[[0.06428619 0.59929061 0.04285699 0.24822687 0.        ]]
ori-tar:[[0.93571383 0.59929061 0.04285699 0.24822687 0.        ]]
0 0.9357138276100159 0.5992906093597412 0.042856987565755844 0.24822686612606049

shape1_103_aug9_aug4
[[0.93571383 0.59929061 0.04285699 0.24822687 0.        ]]
ori-tar:[[0.26217598 0.28985485 0.40097338 0.39130431 0.        ]]
0 0.262175977230072 0.28985485434532166 0.400973379611969 0.3913043141365051

shape1_113_aug1_aug3
[[0.26217598 0.28985485 0.40097338 0.39130431 0.        ]]
ori-tar:[[0.73782402 0.28985485 0.40097338 0.39130431 0.        ]]
0 0.737824022769928 0.28985485434532166 0.400973379611969 0.3913043141365051

shape1_113_aug1_aug4
[[0.73782402 0.28985485 0.40097338 0.39130431 0.        ]]
ori-tar:[[0.5935356  0.71500015 0.33975187 0.26999998 0.        ]]
0 0.5935356020927429 0.7

ori-tar:[[0.20676558 0.61809087 0.12782024 0.19095522 0.        ]]
0 0.2067655771970749 0.6180908679962158 0.1278202384710312 0.19095522165298462

shape1_129_aug16_aug4
[[0.20676558 0.61809087 0.12782024 0.19095522 0.        ]]
ori-tar:[[0.04362051 0.35714245 0.04784266 0.193878   0.        ]]
0 0.0436205118894577 0.35714244842529297 0.047842659056186676 0.19387799501419067

shape1_129_aug17_aug3
[[0.04362051 0.35714245 0.04784266 0.193878   0.        ]]
ori-tar:[[0.95637947 0.64285755 0.04784266 0.193878   0.        ]]
0 0.9563794732093811 0.642857551574707 0.047842659056186676 0.19387799501419067

shape1_129_aug17_aug4
[[0.95637947 0.64285755 0.04784266 0.193878   0.        ]]
ori-tar:[[0.95818245 0.70813435 0.06181851 0.1818186  0.        ]]
0 0.9581824541091919 0.7081343531608582 0.06181851401925087 0.18181860446929932

shape1_129_aug18_aug3
[[0.95818245 0.70813435 0.06181851 0.1818186  0.        ]]
ori-tar:[[0.95818245 0.29186565 0.06181851 0.1818186  0.        ]]
0 0.958182454109

ori-tar:[[0.73439491 0.65088844 0.22292988 0.46153843 0.        ]]
0 0.734394907951355 0.6508884429931641 0.22292988002300262 0.4615384340286255

shape1_13_aug21_aug3
[[0.73439491 0.65088844 0.22292988 0.46153843 0.        ]]
ori-tar:[[0.26560509 0.34911159 0.22292988 0.46153843 0.        ]]
0 0.265605092048645 0.3491115868091583 0.22292988002300262 0.4615384340286255

shape1_13_aug21_aug4
[[0.26560509 0.34911159 0.22292988 0.46153843 0.        ]]
ori-tar:[[0.43295455 0.60274065 0.39772719 0.53424656 0.        ]]
0 0.4329545497894287 0.6027406454086304 0.39772719144821167 0.534246563911438

shape1_13_aug22_aug3
[[0.43295455 0.60274065 0.39772719 0.53424656 0.        ]]
ori-tar:[[0.43295455 0.60274065 0.39772719 0.53424656 0.        ]]
0 0.4329545497894287 0.6027406454086304 0.39772719144821167 0.534246563911438

shape1_13_aug22_aug4
[[0.43295455 0.60274065 0.39772719 0.53424656 0.        ]]
ori-tar:[[0.23805733 0.77695221 0.27866235 0.2899628  0.        ]]
0 0.23805733025074005 0.77695

ori-tar:[[0.28480917 0.42138344 0.18987428 0.26415169 0.        ]]
0 0.2848091721534729 0.42138344049453735 0.18987427651882172 0.2641516923904419

shape1_151_aug22_aug3
[[0.28480917 0.42138344 0.18987428 0.26415169 0.        ]]
ori-tar:[[0.28480917 0.42138344 0.18987428 0.26415169 0.        ]]
0 0.2848091721534729 0.42138344049453735 0.18987427651882172 0.2641516923904419

shape1_151_aug22_aug4
[[0.28480917 0.42138344 0.18987428 0.26415169 0.        ]]
ori-tar:[[0.08103675 0.85340327 0.09724517 0.21989591 0.        ]]
0 0.08103674650192261 0.8534032702445984 0.09724517166614532 0.21989591419696808

shape1_151_aug23_aug3
[[0.08103675 0.85340327 0.09724517 0.21989591 0.        ]]
ori-tar:[[0.08103675 0.14659673 0.09724517 0.21989591 0.        ]]
0 0.08103674650192261 0.1465967297554016 0.09724517166614532 0.21989591419696808

shape1_151_aug23_aug4
[[0.08103675 0.14659673 0.09724517 0.21989591 0.        ]]
ori-tar:[[0.54887187 0.59999979 0.06444712 0.33600095 0.        ]]
0 0.54887187480

...

ori-tar:[[0.3237192  0.4690271  0.45512453 0.37168118 0.        ]]
0 0.32371920347213745 0.4690271019935608 0.45512452721595764 0.37168118357658386

shape3_87_aug12_aug3
[[0.3237192  0.4690271  0.45512453 0.37168118 0.        ]]
ori-tar:[[0.3237192  0.5309729  0.45512453 0.37168118 0.        ]]
0 0.32371920347213745 0.5309728980064392 0.45512452721595764 0.37168118357658386

shape3_87_aug12_aug4
[[0.3237192  0.5309729  0.45512453 0.37168118 0.        ]]
ori-tar:[[0.14799976 0.45502681 0.0811422  0.22222209 0.        ]]
0 0.14799976348876953 0.4550268054008484 0.08114220201969147 0.22222208976745605

shape3_87_aug13_aug3
[[0.14799976 0.45502681 0.0811422  0.22222209 0.        ]]
ori-tar:[[0.14799976 0.45502681 0.0811422  0.22222209 0.        ]]
0 0.14799976348876953 0.4550268054008484 0.08114220201969147 0.22222208976745605

shape3_87_aug13_aug4
[[0.14799976 0.45502681 0.0811422  0.22222209 0.        ]]
ori-tar:[[0.33059144 0.52112633 0.23355074 0.29577446 0.        ]]
0 0.3305914402008

ori-tar:[[0.09913349 0.52093369 0.07707129 0.21376383 0.        ]]
0 0.09913349151611328 0.5209336876869202 0.07707129418849945 0.21376383304595947

shape4_19_aug21_aug4
[[0.09913349 0.52093369 0.07707129 0.21376383 0.        ]]
ori-tar:[[0.19867545 0.58417702 0.06110009 0.16504894 0.        ]]
0 0.19867545366287231 0.5841770172119141 0.06110008805990219 0.16504894196987152

shape4_19_aug22_aug3
[[0.19867545 0.58417702 0.06110009 0.16504894 0.        ]]
ori-tar:[[0.19867545 0.41582295 0.06110009 0.16504894 0.        ]]
0 0.19867545366287231 0.41582295298576355 0.06110008805990219 0.16504894196987152

shape4_19_aug22_aug4
[[0.19867545 0.41582295 0.06110009 0.16504894 0.        ]]
ori-tar:[[0.14925021 0.70263672 0.12444845 0.36760902 0.        ]]
0 0.14925020933151245 0.70263671875 0.12444844841957092 0.36760902404785156

shape4_19_aug23_aug3
[[0.14925021 0.70263672 0.12444845 0.36760902 0.        ]]
ori-tar:[[0.14925021 0.29736325 0.12444845 0.36760902 0.        ]]
0 0.14925020933151245

ori-tar:[[0.10659665 0.83225793 0.05066888 0.28386974 0.        ]]
0 0.10659664869308472 0.8322579264640808 0.050668880343437195 0.28386974334716797

shape5_20_aug26_aug4
[[0.10659665 0.83225793 0.05066888 0.28386974 0.        ]]
ori-tar:[[0.65868986 0.65581387 0.13350038 0.20465028 0.        ]]
0 0.6586898565292358 0.6558138728141785 0.1335003823041916 0.20465028285980225

shape5_20_aug27_aug3
[[0.65868986 0.65581387 0.13350038 0.20465028 0.        ]]
ori-tar:[[0.34131014 0.34418613 0.13350038 0.20465028 0.        ]]
0 0.34131014347076416 0.34418612718582153 0.1335003823041916 0.20465028285980225

shape5_20_aug27_aug4
[[0.34131014 0.34418613 0.13350038 0.20465028 0.        ]]
ori-tar:[[0.82100379 0.5217393  0.07001275 0.38260707 0.        ]]
0 0.821003794670105 0.5217393040657043 0.07001274824142456 0.3826070725917816

shape5_20_aug28_aug3
[[0.82100379 0.5217393  0.07001275 0.38260707 0.        ]]
ori-tar:[[0.17899621 0.4782607  0.07001275 0.38260707 0.        ]]
0 0.17899620532989502

ori-tar:[[0.43689591 0.80882299 0.40776777 0.09893008 0.        ]]
0 0.4368959069252014 0.8088229894638062 0.40776777267456055 0.09893008321523666

shape5_8_aug28_aug3
[[0.43689591 0.80882299 0.40776777 0.09893008 0.        ]]
ori-tar:[[0.56310409 0.80882299 0.40776777 0.09893008 0.        ]]
0 0.5631040930747986 0.8088229894638062 0.40776777267456055 0.09893008321523666

shape5_8_aug28_aug4
[[0.56310409 0.80882299 0.40776777 0.09893008 0.        ]]
ori-tar:[[0.84634215 0.82361901 0.10243922 0.11349647 0.        ]]
0 0.846342146396637 0.82361900806427 0.10243922472000122 0.11349647492170334

shape5_8_aug29_aug3
[[0.84634215 0.82361901 0.10243922 0.11349647 0.        ]]
ori-tar:[[0.15365785 0.82361901 0.10243922 0.11349647 0.        ]]
0 0.15365785360336304 0.82361900806427 0.10243922472000122 0.11349647492170334

shape5_8_aug29_aug4
[[0.15365785 0.82361901 0.10243922 0.11349647 0.        ]]
ori-tar:[[0.28185824 0.50510412 0.12593727 0.3775495  0.        ]]
0 0.2818582355976105 0.505104

ori-tar:[[0.33585048 0.65870267 0.07036878 0.15914172 0.        ]]
0 0.33585047721862793 0.6587026715278625 0.07036878168582916 0.15914171934127808

shape6_9_aug32_aug3
[[0.33585048 0.65870267 0.07036878 0.15914172 0.        ]]
ori-tar:[[0.66414952 0.34129733 0.07036878 0.15914172 0.        ]]
0 0.6641495227813721 0.34129732847213745 0.07036878168582916 0.15914171934127808

shape6_9_aug32_aug4
[[0.66414952 0.34129733 0.07036878 0.15914172 0.        ]]
ori-tar:[[0.76072145 0.66261542 0.16631213 0.15232135 0.        ]]
0 0.7607214450836182 0.6626154184341431 0.16631212830543518 0.15232135355472565

shape6_9_aug33_aug3
[[0.76072145 0.66261542 0.16631213 0.15232135 0.        ]]
ori-tar:[[0.76072145 0.33738458 0.16631213 0.15232135 0.        ]]
0 0.7607214450836182 0.33738458156585693 0.16631212830543518 0.15232135355472565

shape6_9_aug33_aug4
[[0.76072145 0.33738458 0.16631213 0.15232135 0.        ]]
ori-tar:[[0.28381282 0.54959047 0.13531488 0.21218896 0.        ]]
0 0.28381282091140747 

In [14]:
len(trainset_IP_AUG)

21000

In [12]:
@interact(index=(0, len(trainset_IP_AUG)-1))

def show_sample(index=0):
    image, target, filename = trainset_IP_AUG[index]
#     image=image.permute(1,2,0).numpy()
    print(f"before cal target:\n{target}")
    img_H, img_W, _ = image.shape
    print(filename)
    print(image.shape)
#     print(image)

#     bboxes = target['boxes']
#     class_ids = target["labels"]
    
    ###
    bboxes = target[:, 0:4]
    class_ids = target[:, 4]
    ###
    bboxes[:, [0,2]] *= img_W
    bboxes[:, [1,3]] *= img_H
    
    print(bboxes)

    canvas = visualize(image, bboxes, class_ids)
    plt.figure(figsize=(6,6))
    plt.imshow(canvas)
    plt.axis('off')
    plt.show()

# show_sample()

interactive(children=(IntSlider(value=0, description='index', max=10499), Output()), _dom_classes=('widget-int…

In [15]:
@interact(index=(0, len(trainset_IP_AUG)-1))

def show_sample(index=0):
    image, target, filename = trainset_IP_AUG[index]
#     image=image.permute(1,2,0).numpy()
    print(f"before cal target:\n{target}")
    img_H, img_W, _ = image.shape
    print(filename)
    print(image.shape)
#     print(image)

#     bboxes = target['boxes']
#     class_ids = target["labels"]
    
    ###
    bboxes = target[:, 0:4]
    class_ids = target[:, 4]
    ###
    bboxes[:, [0,2]] *= img_W
    bboxes[:, [1,3]] *= img_H
    
    print(bboxes)

    canvas = visualize(image, bboxes, class_ids)
    plt.figure(figsize=(6,6))
    plt.imshow(canvas)
    plt.axis('off')
    plt.show()

# show_sample()

interactive(children=(IntSlider(value=0, description='index', max=20999), Output()), _dom_classes=('widget-int…